# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [15 EVs per week test]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f1abafe8250>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 15
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 15, 'EVs_n_max': 783, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energ

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13536.1 , over-consume=kWh  31247.55 , under-consume=kWh  17711.44 , Total_cost=€  602.95 , overcost=€  1105.21 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [ ]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13755.21 , over-consume=kWh  32206.97 , under-consume=kWh  18451.77 , Total_cost=€  633.36 , overcost=€  1154.86 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -5649.51 , over-consume=KWh  3096.72 , under-consume=KWh  8746.23 , Total_cost=€  -110.85 , Overcost=€  108.41 
 EV_INFO: Av.EV_energy_leaving=kWh  70.37 , Std.EV_energy_leaving=kWh  23.95 , EV_departures =  784 , EV_queue_left =  0
SCORE:  Cumulative_reward= 327883.8 - Step_rewars (load_t= 300100.1, EVs_energy_t= 19479.92)
 - Final_rewards (EVs_energy= 14384.95, Overconsume= -3108.19, Underconsume= -5137.6, Overcost= 2164.6)
Episode:1 Score:327883.7961868358


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  48.419044   0.000000   0.000000  55.644783   
2022-01-01 00:15:00  48.669044   0.000000   0.000000  54.585907   
2022-01-01 00:30:00  48.919044   0.000000   0.000000  53.605774   
2022-01-01 00:45:00  49.169044   0.000000   0.000000  53.173897   
2022-01-01 01:00:00  49.419044   0.000000   0.000000  52.715652   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  87.112320  43.749439  81.973145  66.836662   
2022-06-06 05:00:00  88.177155  43.499439  83.037979  67.901497   
2022-06-06 05:15:00  89.260612  43.249439  84.121437  68.984955   
2022-06-06 05:30:00  90.375549  42.999439  85.236374  70.099892   
2022-06-06 05:45:00  91.483788  42.749439  86.344612  71.208130   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [1, 2, 2, 2]   
2022-01-01 00:15:00          [11739, 0, 0, 11738]  [1, 2, 2, 2]   
2022-01-01 00:30:00          [11739, 0, 0, 11738]  [1, 2, 2, 2]   
2022-01-01 00:45:00          [11739, 0, 0, 11738]  [1, 2, 2, 2]   
2022-01-01 01:00:00          [11739, 0, 0, 11738]  [1, 2, 2, 2]   
...                                           ...           ...   
2022-06-06 04:45:00  [12075, 12076, 12073, 12074]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [12075, 12076, 12073, 12074]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [12075, 12076, 12073, 12074]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [12075, 12076, 12073, 12074]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [12075, 12076, 12073, 12074]  [1, 2, 1, 1]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False]  2.017472e+00         15.0   
2022-01-01 00:15:00   [False, False, False, True]  0.000000e+00         15.0   
2022-01-01 00:30:00   [False, False, False, True]  0.000000e+00         15.0   
2022-01-01 00:45:00   [False, False, False, True]  0.000000e+00         15.0   
2022-01-01 01:00:00   [False, False, False, True]  1.110223e-16         15.0   
...                                           ...           ...          ...   
2022-06-06 04:45:00     [True, False, True, True]  0.000000e+00         15.0   
2022-06-06 05:00:00     [True, False, True, True]  0.000000e+00         15.0   
2022-06-06 05:15:00     [True, False, True, True]  0.000000e+00         15.0   
2022-06-06 05:30:00     [True, False, True, True]  0.000000e+00         15.0   
2022-06-06 05:45:00    [False, False, True, True]  0.000000e+00         15.0   

                     EV_reward  rewards  
time                                     
2022-01-01 00:00:00        0.0     15.0  
2022-01-01 00:15:00        0.0     15.0  
2022-01-01 00:30:00        0.0     15.0  
2022-01-01 00:45:00        0.0     15.0  
2022-01-01 01:00:00        0.0     15.0  
...                        ...      ...  
2022-06-06 04:45:00        0.0     15.0  
2022-06-06 05:00:00        0.0     15.0  
2022-06-06 05:15:00        0.0     15.0  
2022-06-06 05:30:00        0.0     15.0  
2022-06-06 05:45:00        0.0     15.0  

[15000 rows x 11 columns]

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 12523, Arrival time: 2022-01-01 16:15:00, Parking_time: 24, Leaving_time: 2022-01-02 16:15:00, SOC: 0.3937226639622907, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 13305, Arrival time: 2022-12-31 14:30:00, Parking_time: 24, Leaving_time: 2023-01-01 14:30:00, SOC: 0.6623529995930447, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  4806.6 , over-consume=kWh  28037.85 , under-consume=kWh  23231.25 , Total_cost=€  297.85 , overcost=€  1243.45 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  91.15


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  5471.86 , over-consume=kWh  28377.68 , under-consume=kWh  22905.82 , Total_cost=€  332.56 , overcost=€  1254.72 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  91.15
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -10011.08 , over-consume=KWh  1902.44 , under-consume=KWh  11913.53 , Total_cost=€  -389.2 , Overcost=€  81.82 
 EV_INFO: Av.EV_energy_leaving=kWh  75.76 , Std.EV_energy_leaving=kWh  22.24 , EV_departures =  781 , EV_queue_left =  0
SCORE:  Cumulative_reward= 329858.85 - Step_rewars (load_t= 283092.66, EVs_energy_t= 32037.48)
 - Final_rewards (EVs_energy= 15040.26, Overconsume= -1920.01, Underconsume= -6002.05, Overcost= 7610.5)
Episode:1 Score:329858.8490928488


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1    2    3                EVs_id  \
time                                                                        
2022-01-01 00:00:00   0.000000   0.000000  0.0  0.0          [0, 0, 0, 0]   
2022-01-01 00:15:00   0.000000   0.000000  0.0  0.0          [0, 0, 0, 0]   
2022-01-01 00:30:00   0.000000   0.000000  0.0  0.0          [0, 0, 0, 0]   
2022-01-01 00:45:00   0.000000   0.000000  0.0  0.0          [0, 0, 0, 0]   
2022-01-01 01:00:00   0.000000   0.000000  0.0  0.0          [0, 0, 0, 0]   
...                        ...        ...  ...  ...                   ...   
2022-06-06 04:45:00  98.489998  75.119308  0.0  0.0  [14428, 14429, 0, 0]   
2022-06-06 05:00:00  99.989998  76.936409  0.0  0.0  [14428, 14429, 0, 0]   
2022-06-06 05:15:00  99.989998  78.812843  0.0  0.0  [14428, 14429, 0, 0]   
2022-06-06 05:30:00  99.989998  80.611946  0.0  0.0  [14428, 14429, 0, 0]   
2022-06-06 05:45:00  99.989998  82.497215  0.0  0.0  [14428, 14429, 0, 0]   

                          actions                    mask_truth      load  \
time                                                                        
2022-01-01 00:00:00  [2, 1, 1, 0]   [False, False, False, True] -3.706720   
2022-01-01 00:15:00  [2, 2, 1, 2]  [False, False, False, False] -5.099080   
2022-01-01 00:30:00  [2, 1, 1, 0]   [False, False, False, True] -4.113859   
2022-01-01 00:45:00  [2, 1, 1, 0]   [False, False, False, True] -2.072151   
2022-01-01 01:00:00  [2, 0, 1, 0]    [False, True, False, True] -4.536019   
...                           ...                           ...       ...   
2022-06-06 04:45:00  [1, 1, 2, 2]   [False, True, False, False] -0.023276   
2022-06-06 05:00:00  [1, 1, 2, 2]   [False, True, False, False] -1.268387   
2022-06-06 05:15:00  [1, 1, 2, 2]   [False, True, False, False] -7.505742   
2022-06-06 05:30:00  [1, 1, 2, 2]   [False, True, False, False] -7.196406   
2022-06-06 05:45:00  [1, 1, 2, 2]   [False, True, False, False] -7.541058   

                     load_reward  EV_reward   rewards  
time                                                   
2022-01-01 00:00:00    -5.999164        0.0 -5.999164  
2022-01-01 00:15:00    -5.103508        0.0 -5.103508  
2022-01-01 00:30:00    -1.786918        0.0 -1.786918  
2022-01-01 00:45:00    -5.487290        0.0 -5.487290  
2022-01-01 01:00:00    -6.110019        0.0 -6.110019  
...                          ...        ...       ...  
2022-06-06 04:45:00    -0.447311        0.0 -0.447311  
2022-06-06 05:00:00    -8.187038        0.0 -8.187038  
2022-06-06 05:15:00    -7.905823        0.0 -7.905823  
2022-06-06 05:30:00    -8.219143        0.0 -8.219143  
2022-06-06 05:45:00    -8.121068        0.0 -8.121068  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 14872, Arrival time: 2022-01-01 06:15:00, Parking_time: 22.983644821988896, Leaving_time: 2022-01-02 05:14:01.121359, SOC: 0.5962062657421249, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 15654, Arrival time: 2022-12-31 13:45:00, Parking_time: 23.677326105026616, Leaving_time: 2023-01-01 13:25:38.373978, SOC: 0.5442431587218415, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  1059.66 , over-consume=kWh  26165.36 , under-consume=kWh  25105.7 , Total_cost=€  199.12 , overcost=€  1110.37 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  95.56


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  1325.29 , over-consume=kWh  26345.94 , under-consume=kWh  25020.65 , Total_cost=€  188.25 , overcost=€  1100.45 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  95.56
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -12886.79 , over-consume=KWh  1289.54 , under-consume=KWh  14176.32 , Total_cost=€  -438.8 , Overcost=€  56.03 
 EV_INFO: Av.EV_energy_leaving=kWh  76.73 , Std.EV_energy_leaving=kWh  22.03 , EV_departures =  781 , EV_queue_left =  0
SCORE:  Cumulative_reward= 315812.3 - Step_rewars (load_t= 266382.69, EVs_energy_t= 33688.35)
 - Final_rewards (EVs_energy= 13470.2, Overconsume= -1181.48, Underconsume= -6873.47, Overcost= 10326.0)
Episode:1 Score:315812.29880085983


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0    1          2          3  \
time                                                        
2022-01-01 00:00:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:15:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:30:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:45:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 01:00:00   0.000000  0.0   0.000000   0.000000   
...                        ...  ...        ...        ...   
2022-06-06 03:30:00  61.249958  0.0  99.989998  35.278496   
2022-06-06 03:45:00  61.249958  0.0  99.989998  35.755299   
2022-06-06 04:00:00  61.249958  0.0  99.989998  36.755249   
2022-06-06 04:15:00  61.249958  0.0  99.989998  37.438484   
2022-06-06 04:30:00  61.249958  0.0  99.989998  38.278316   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 03:30:00  [16775, 0, 16774, 16776]  [0, 2, 1, 1]   
2022-06-06 03:45:00  [16775, 0, 16774, 16776]  [0, 2, 1, 1]   
2022-06-06 04:00:00  [16775, 0, 16774, 16776]  [0, 2, 1, 1]   
2022-06-06 04:15:00  [16775, 0, 16774, 16776]  [0, 2, 1, 1]   
2022-06-06 04:30:00  [16775, 0, 16774, 16776]  [0, 2, 1, 1]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, False, False, True] -3.498390    -3.567320   
2022-01-01 00:15:00  [False, False, False, True] -3.140392    -4.466562   
2022-01-01 00:30:00  [False, False, False, True] -3.679937    -4.879212   
2022-01-01 00:45:00   [False, True, False, True] -3.927527    -5.330206   
2022-01-01 01:00:00   [False, True, False, True] -4.363227    -5.623679   
...                                          ...       ...          ...   
2022-06-06 03:30:00   [True, False, False, True] -1.544542    -1.512009   
2022-06-06 03:45:00   [True, False, False, True] -1.907206    -4.999650   
2022-06-06 04:00:00   [True, False, False, True] -3.999790    -2.888223   
2022-06-06 04:15:00   [True, False, False, True] -2.732934    -3.932193   
2022-06-06 04:30:00   [True, False, False, True] -3.359316    -4.046319   

                     EV_reward   rewards  
time                                      
2022-01-01 00:00:00        0.0 -3.567320  
2022-01-01 00:15:00        0.0 -4.466562  
2022-01-01 00:30:00        0.0 -4.879212  
2022-01-01 00:45:00        0.0 -5.330206  
2022-01-01 01:00:00        0.0 -5.623679  
...                        ...       ...  
2022-06-06 03:30:00        0.0 -1.512009  
2022-06-06 03:45:00        0.0 -4.999650  
2022-06-06 04:00:00        0.0 -2.888223  
2022-06-06 04:15:00        0.0 -3.932193  
2022-06-06 04:30:00        0.0 -4.046319  

[14995 rows x 11 columns]

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()